In [110]:
from itertools import combinations
from collections import namedtuple
import numpy as np
from icecream import ic
import random

## Simple Test Problem

In [111]:
CITIES = [
    "Rome",
    "Milan",
    "Naples",
    "Turin",
    "Palermo",
    "Genoa",
    "Bologna",
    "Florence",
    "Bari",
    "Catania",
    "Venice",
    "Verona",
    "Messina",
    "Padua",
    "Trieste",
    "Taranto",
    "Brescia",
    "Prato",
    "Parma",
    "Modena",
]
test_problem = np.load('lab2/test_problem.npy')
problem = test_problem


In [112]:
Individual = namedtuple('individual', ['genotype', 'weight'])

## Common tests

In [4]:
problem = np.load('lab2/problem_r2_100.npy')

In [5]:
# Negative values?
np.any(problem < 0)

np.True_

In [6]:
# Diagonal is all zero?
np.allclose(np.diag(problem), 0.0)

False

In [7]:
# Symmetric matrix?
np.allclose(problem, problem.T)

False

In [8]:
# Triangular inequality
all(
    problem[x, y] <= problem[x, z] + problem[z, y]
    for x, y, z in list(combinations(range(problem.shape[0]), 3))
)

False

# Solution

In [113]:
POPULATION_SIZE = 10
OFFSPRING_SIZE = 5
MUTATION_RATE = 0.2

In [114]:
# Create a greedy solution starting from a random node
def greedy_solution(problem: np.ndarray, start_node: int, randomization: float = 0.2) -> list:
    solution = [start_node]
    unvisited_nodes = list(range(problem.shape[0]))
    unvisited_nodes.remove(start_node)
    while len(unvisited_nodes) > 0:
        if np.random.rand() < randomization:
            next_node = int(np.random.choice(list(unvisited_nodes)))
        else:
            last_node = solution[-1]
            min_distance = float('inf')
            next_node = None
            for node in unvisited_nodes:
                distance = problem[last_node, node]
                if distance < min_distance:
                    min_distance = distance
                    next_node = node
        
        unvisited_nodes.remove(next_node)
        solution.append(next_node)
    
    return solution


In [ ]:
def compute_weight(problem: np.ndarray, solution: list) -> float:
    weight = 0.0
    for i in range(len(solution)-1):
        weight += problem[solution[i], solution[i+1]]
    weight += problem[solution[-1], solution[0]]  # Return to start
    return weight

def mutation(solution: Individual, problem: np.ndarray, n_mutations: int = 1) -> Individual:
    new_solution = solution.genotype.copy()
    for _ in range(n_mutations):
        # Select two different indices
        nodes = random.sample(range(len(solution)), 2)
        # Swap
        new_solution[nodes[0]], new_solution[nodes[1]] = new_solution[nodes[1]], new_solution[nodes[0]]
    return Individual(genotype=new_solution, weight=compute_weight(problem, new_solution))

def crossover(parent1: Individual, parent2: Individual, problem: np.ndarray) -> Individual:
    # TODO: test if this is a good crossover method
    new_solution = []
    index1 = 1
    index2 = 1
    turn = 1

    # both parents start with the same node (0)
    new_solution.append(parent1.genotype[0])
    not_included = list(not_included)[1:]

    while True:
        # pick nodes drom parent 1, then when we encounter the node which is in parent2.genotype[1] we start picking from parent 2
        # Then again we switch when we encounter the node which is in parent1.genotype[index1]
        if turn%2 == 1:
            new_solution.append(parent1.genotype[index1])
            not_included.remove(parent1.genotype[index1])
            if parent1.genotype[index1] == parent2.genotype[index2]:
                turn += 1
            index1 += 1
        else:
            new_solution.append(parent2.genotype[index2])
            not_included.remove(parent2.genotype[index2])
            if parent2.genotype[index2] == parent1.genotype[index1]:
                turn += 1
            index2 += 1

        if len(new_solution) == len(parent1.genotype):
            break

    return Individual(genotype=new_solution, weight=compute_weight(problem, new_solution))

In [116]:
def tournament_selection(population: list, tournament_size: int = 2) -> Individual:
    tournament = random.sample(population, tournament_size)
    return min(tournament, key=lambda ind: ind.weight)

In [117]:
def print_test_solution(solution: list):
    for i, city_ind in enumerate(solution):
        print(f"{CITIES[city_ind]} --{test_problem[city_ind, solution[(i+1) % len(solution)]]}--> ", end="")
        if (i+1)%4==0:
            print()
    print(f"Total distance: {compute_weight(test_problem, solution)}")

In [143]:
# Create a population of random greedy solutions
def create_population(problem: np.ndarray, randomization: float = 0.2) -> list:
    population = []
    for _ in range(POPULATION_SIZE):
        start_node = random.randint(0, problem.shape[0]-1)
        solution = greedy_solution(problem, start_node, randomization)

        # After creating agreedy solution starting from the node start_node I want to "normalize" it
        # so that all solutions start from node 0, even though they are composed by different sequences of nodes
        idx_start = solution.index(0)
        solution = solution[idx_start:] + solution[:idx_start]
        
        # After that we can compute the weight
        weight = compute_weight(problem, solution)
        population.append(Individual(genotype=solution, weight=weight))

    return population


In [ ]:
def evolutionary_algorithm(problem: np.ndarray, 
                           generations: int = 1000,
                           mutation_rate: float = MUTATION_RATE,
                           initial_randomization: float = 0.2) -> list:
    
    population = create_population(problem, initial_randomization)
    best_solution = Individual(genotype=None, weight=float('inf'))

    for generation in range(generations):
        offsprings = []

        # generatin of the offsprings
        for _ in range(OFFSPRING_SIZE):
            if np.random.rand() < mutation_rate:
                # Mutation
                parent = tournament_selection(population, tournament_size=2)
                offspring = mutation(parent, problem, n_mutations=random.randint(1,5))      # do from 1 up to 5 swaps in a mutation
            else:
                # Crossover
                parent1 = tournament_selection(population)
                parent2 = tournament_selection(population)
                # TODO: implement crossover
                pass
            offsprings.append(offspring)

        # Add the offsprings to the population
        # Steady state approach
        population.extend(offsprings)
        
        # Sort the population by weight
        population.sort(key=lambda ind: ind.weight)
        population = population[:POPULATION_SIZE]

        # Clear the offsprings list
        offsprings = []

        ic(population[0].weight, population[-1].weight)

        # Keep track of the best solution
        if population[0].weight < best_solution.weight:
            best_solution = population[0]
            
    

evolutionary_algorithm(problem, generations=10000, mutation_rate=1, initial_randomization=1)

ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(9538.66)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(8660.24)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(8139.259999999999)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(7355.98)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(7355.98)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(6428.1900000000005)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(6428.1900000000005)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(6428.1900000000005)
ic| population[0].weight: np.float64(6428.1900000000005)
    population[-1].weight: np.float64(6428.1900000000005)
ic| popula